In [1]:
%matplotlib inline
from matplotlib import pyplot as plt
from matplotlib import style
from numpy.random import randint, randn
import pandas as pd


In [3]:
md = pd.read_table('manuscript-package/1250/ag_map_with_alpha.txt', dtype={'#SampleID': str}).query('country=="USA"')
md.set_index('#SampleID', inplace=True)

/Users/zech/miniconda3/envs/folium/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2698: DtypeWarning: Columns (66) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [4]:
income = pd.read_csv('/Users/zech/database/census/SAIPESNC_25OCT17_19_27_20_88.csv', dtype={'County ID': str})

In [5]:
income['Median Household Income in Dollars'] = income['Median Household Income in Dollars'].str.replace(',', '').str.replace('$', '').astype(float)

In [6]:
income.head()

Year  State County ID  State / County Name All Ages SAIPE Poverty Universe  \
0  2015      1     01001  Autauga County (AL)                          54,860   
1  2015      1     01003  Baldwin County (AL)                         201,006   
2  2015      1     01005  Barbour County (AL)                          23,066   
3  2015      1     01007     Bibb County (AL)                          20,326   
4  2015      1     01009   Blount County (AL)                          57,116   

  All Ages in Poverty Count All Ages in Poverty Count LB 90%  \
0                     6,966                            5,673   
1                    25,941                           21,665   
2                     7,380                            6,240   
3                     4,516                            3,584   
4                     8,399                            6,798   

  All Ages in Poverty Count UB 90%  \
0                            8,259   
1                           30,217   
2                            8,520   
3                            5,448   
4                           10,000   

  90% Confidence Interval (All Ages in Poverty Count)  \
0                                     5,673 to 8,259    
1                                   21,665 to 30,217    
2                                     6,240 to 8,520    
3                                     3,584 to 5,448    
4                                    6,798 to 10,000    

   All Ages in Poverty Percent  \
0                         12.7   
1                         12.9   
2                         32.0   
3                         22.2   
4                         14.7   

                               ...                               \
0                              ...                                
1                              ...                                
2                              ...                                
3                              ...                                
4                              ...                                

   Under Age 5 in Poverty Count UB 90%  \
0                                  NaN   
1                                  NaN   
2                                  NaN   
3                                  NaN   
4                                  NaN   

   90% Confidence Interval (Under Age 5 in Poverty Count)  \
0                                                NaN        
1                                                NaN        
2                                                NaN        
3                                                NaN        
4                                                NaN        

  Under Age 5 in Poverty Percent Under Age 5 in Poverty Percent LB 90%  \
0                            NaN                                   NaN   
1                            NaN                                   NaN   
2                            NaN                                   NaN   
3                            NaN                                   NaN   
4                            NaN                                   NaN   

  Under Age 5 in Poverty Percent UB 90%  \
0                                   NaN   
1                                   NaN   
2                                   NaN   
3                                   NaN   
4                                   NaN   

  90% Confidence Interval (Under Age 5 in Poverty Percent)  \
0                                                NaN         
1                                                NaN         
2                                                NaN         
3                                                NaN         
4                                                NaN         

  Median Household Income in Dollars  \
0                            56580.0   
1                            52387.0   
2                            31433.0   
3                            40767.0   
4                            50487.0   

  Median Hous

## render the background map

In [76]:
import folium
from folium import plugins
import branca

employed_series = income.set_index('County ID')['Median Household Income in Dollars'].dropna()
colorscale = branca.colormap.linear.YlGnBu.scale(employed_series.min(), employed_series.max())

county_geo = 'us-counties_topo.json'
def style_function(feature):
    employed = employed_series.get(feature['id'][-5:], None)
    return {
        'fillOpacity': 0.7,
        'weight': 0,
        'fillColor': '#black' if employed is None else colorscale(employed)
    }


m = folium.Map(
    location=[48, -102],
    #tiles='Stamen Terrain',
    #tiles='stamentoner', 
    #tiles='cartodbpositron',
    zoom_start=4
)

folium.TopoJson(
    open(county_geo),
    'objects.us_counties_20m',
    name='2015 median house income',
    style_function=style_function
).add_to(m)

colorscale.caption = 'income color scale'
colorscale.add_to(m)

m

In [68]:
# add more tile options
folium.TileLayer('Stamen Terrain').add_to(m)
folium.TileLayer('Stamen Toner').add_to(m)

In [69]:
m.save('/tmp/income.html')

## add AGP icon

In [70]:
# add fullscreen button
plugins.Fullscreen(
    position='topright',
    title='Expand me',
    title_cancel='Exit me',
    force_separate_button=True).add_to(m)

In [71]:
from folium.plugins import FloatImage
url = 'https://d30pl5hav4s8uw.cloudfront.net/organizations/97e330a9575c484cbe0a7581f448be9f.png'
FloatImage(url, bottom=80, left=30).add_to(m)
m

## Add sample location layer

In [72]:
lon=pd.to_numeric(md['longitude'], errors='coerce')
lat=pd.to_numeric(md['latitude'], errors='coerce')
data = pd.concat([lat, lon], axis=1)
data.index = md.index.astype(str)
data = data.dropna()
data.shape

(6376, 2)

In [73]:
marker_cluster = MarkerCluster(
    locations=data.values.tolist(),
    popups=data.index.tolist(),
    name='sample locations',
    overlay=True,
    control=True)
marker_cluster.add_to(m)


In [74]:
folium.LayerControl().add_to(m)

In [75]:
m.save('/tmp/income-sample.html')

In [15]:
md.loc['10317.000066448', ['latitude','longitude']]

latitude       34.7
longitude    -118.3
Name: 10317.000066448, dtype: object

## show sample location as heatmap

In [93]:
from folium.plugins import HeatMap
HeatMap(data.values.tolist()).add_to(m)
m